In [1]:
import SNAPy as sna
import geopandas as gpd
import pandas as pd
import warnings
import numpy as np

warnings.filterwarnings('ignore')

MainDir = 'D:\\OneDrive\\0405 IKN Spatial Analyses\\RPK 1BC 2023 Network Analysis\\601 INPUT DATA\\Run01 - 1B\\'
dfNetwork = gpd.read_file(MainDir+'1B_R1_Data.gpkg', layer='NetworkDt') # network dataframe
dfEntries = gpd.read_file(MainDir+'1B_R1_Data.gpkg', layer='EntriesDt') # entrance dataframe


In [8]:
type(dfEntries.columns[0])


str

In [2]:
# Reads Routines
ReachRoutine = pd.read_csv(MainDir+'ReachMeasures.csv')

baseSet = {
        'EntDist' : 100,
        'EntID': 'fid',
        'EdgeID': 'fid',
        'OptSuffix': '',
        'OptPrefix': 'R_',
        'CalcExp': 0.35,
        'CalcComp': 0.6,
        'CalcType': 'NDW',
        'DestWgt': 'Kapasitas',
        'DumpDir': MainDir+'dump',
        'DumpEnt': 'DumpEnt_1B_01.pkl',
        'EntryDtDumpOvr': False,
        'EdgeCost': 'Mult',
        'Threads': 0,
    }

nwSim = sna.GraphSims(dfNetwork, dfEntries, **baseSet)
nwSim = sna.ReachAggregate(nwSim, ReachRoutine, **baseSet) # main class for loading network data


GraphSim Class ----------
Network data is multilinestring, exploded
EntriesDf EntID not detected, adding from index
NetworkDf EdgeID not detected, adding from index
Graph Built
Pickled EntriesPt File Detected, using it instead
Found 1611 Pickled Entry Points at D:\OneDrive\0405 IKN Spatial Analyses\RPK 1BC 2023 Network Analysis\601 INPUT DATA\Run01 - 1B\dump
Starting reach aggregate of 401 relations
	1/401  Reach from Hunian to Amn_PendidikanA
		One or more keys not found
	2/401  Reach from Hunian to Amn_PendidikanB
Reach -------------- As R_Amn_PendidikanB with NDW of Kapasitas
Collected 593 Origin and 44 Destinations Point[s]
Processing with multithreading, with chunksize 27
Multiprocessing gph_Base_Reach_multi, on 43 task chunks
Multiprocessing finished in 2.636 seconds
	3/401  Reach from Hunian to Amn_PendidikanC
Reach -------------- As R_Amn_PendidikanC with NDW of Kapasitas
Collected 593 Origin and 33 Destinations Point[s]
Processing with multithreading, with chunksize 27
Multipr

In [10]:
add = []
for cl in nwSim.EntriesDf.columns:
    if cl[:2] == 'R_':
        add.append(nwSim.EntriesDf[cl])
nwSim.EntriesDf['Reach_Centrality'] = sum(add)

nwSim.EntriesDf['KPI_R_Hunian'] = (nwSim.EntriesDf['R_Amn_PendidikanB']>0)*1 + (nwSim.EntriesDf['R_Amn_Integrasi']>0)*1 + (nwSim.EntriesDf['R_Taman']>0)*1 + ((nwSim.EntriesDf['R_central station']+nwSim.EntriesDf['R_Curbside Station']+nwSim.EntriesDf['R_Amn_Transit'])>0)*1
nwSim.EntriesDf['KPI_R_NonHunian'] = (nwSim.EntriesDf['R_Amn_Integrasi']>0)*1 + (nwSim.EntriesDf['R_Taman']>0)*1 + ((nwSim.EntriesDf['R_central station']+nwSim.EntriesDf['R_Curbside Station']+nwSim.EntriesDf['R_Amn_Transit'])>0)*1



nwSim.EntriesDf.to_file(MainDir+"1B_01_rslt2.gpkg", layer="EntriesReach2", crs="EPSG:32750", driver='GPKG')

In [3]:
BtwnRoutine = pd.read_csv(MainDir+'TitikAkses_Btwn.csv')
BtwnPairs = pd.read_csv(MainDir + 'Pairs_Btwn.csv')


baseSet = {
        'EntDist' : 100,
        'EntID': 'fid',
        'EdgeID': 'fid',
        'OptSuffix': '',
        'OptPrefix': '',
        'DetourR' : 1.2, 
        'AlphaExp' : 0.35,
        'TypeMatch': 'Fungsi',
        'DumpDir': MainDir+'dump',
        'DumpEnt': 'DumpEnt_1B_01.pkl',
        'EntryDtDumpOvr': True,
        'EdgeCost': 'Mult',
        'Threads': 0,
    }

nwSim = sna.GraphSims(dfNetwork, dfEntries, **baseSet) # Restarting nwSim
sna.BetweenessPAggregate(nwSim, BtwnPairs, BtwnRoutine, **baseSet)


GraphSim Class ----------
Network data is multilinestring, exploded
NetworkDf EdgeID not detected, adding from index
Graph Built
Pickled EntriesPt File Detected, using it instead
Found 1611 Pickled Entry Points at D:\OneDrive\0405 IKN Spatial Analyses\RPK 1BC 2023 Network Analysis\601 INPUT DATA\Run01 - 1B\dump
Appending Sim Weights
	Sim Weights added
Starting Betweeness aggregate of 4 relations
	1/4  Reach from S01_O to S01_D
BetweenessPatronage ---------- 
As Sim_01 from S01_O to S01_D
Collected 593 Origin and 44 Destinations Point[s]
Processing with multithreading, with chunksize 14
Multiprocessing gph_Base_BetweenessPatronage_multi, on 43 task chunks
Multiprocessing finished in 5.813 seconds
	2/4  Reach from S02_O to S02_D
BetweenessPatronage ---------- 
As Sim_02 from S02_O to S02_D
Collected 1471 Origin and 140 Destinations Point[s]
Processing with multithreading, with chunksize 32
Multiprocessing gph_Base_BetweenessPatronage_multi, on 46 task chunks
Multiprocessing finished in 5

In [5]:
nwSim.NetworkDf['Btw_Commute'] = (nwSim.NetworkDf['Sim_01'] + nwSim.NetworkDf['Sim_02'])*2
nwSim.NetworkDf['Btw_Activity'] = nwSim.NetworkDf['Sim_03'] + nwSim.NetworkDf['Sim_04']
nwSim.NetworkDf['Btw_Total'] = nwSim.NetworkDf['Btw_Commute'] + nwSim.NetworkDf['Btw_Activity']
nwSim.NetworkDf['Btw_PbTransport'] = nwSim.NetworkDf['Sim_02']*2 + nwSim.NetworkDf['Sim_04']

In [6]:
Settings={
            'SearchDist': 700.0,
            'CalcExp': 0.67,
            'DestWgt': 'Kapasitas',
            'RsltAttr': 'Strg_700',
        }

nwSim.Straightness(**Settings)

Settings={
            'SearchDist': 1200.0,
            'CalcExp': 0.67,
            'DestWgt': 'Kapasitas',
            'RsltAttr': 'Strg_1200',
        }

nwSim.Straightness(**Settings)

Straightness Average -------------
 As Strg_700 of Kapasitas
Collected 1611 Origin and 1611 Destinations Point[s]
Processing with multithreading, with chunksize 71
Multiprocessing gph_Base_Straightness_multi, on 45 task chunks
Multiprocessing finished in 22.487 seconds
Straightness Average -------------
 As Strg_1200 of Kapasitas
Collected 1611 Origin and 1611 Destinations Point[s]
Processing with multithreading, with chunksize 71
Multiprocessing gph_Base_Straightness_multi, on 45 task chunks
Multiprocessing finished in 71.110 seconds


GFA            Fungsi   Kapasitas                        geometry  \
0     17694.0     Amn_Kesehatan  737.250000  POINT (463651.769 9890571.698)   
1      8400.0     Amn_Kesehatan  350.000000  POINT (463544.401 9890487.945)   
2      6480.0  Amn_PelayananSPL  270.000000  POINT (464224.115 9889771.287)   
3      1187.0  Amn_PelayananSPL   49.458333  POINT (464151.626 9889883.661)   
4      2828.0  Amn_PelayananSPL  117.833333  POINT (464235.846 9889718.136)   
...       ...               ...         ...                             ...   
1606    200.0             Taman   12.500000  POINT (466572.311 9889951.999)   
1607    200.0             Taman   12.500000  POINT (466533.684 9889888.050)   
1608    200.0             Taman   12.500000  POINT (466429.820 9889913.802)   
1609    200.0             Taman   12.500000  POINT (466363.296 9889703.929)   
1610    200.0             Taman   12.500000  POINT (466687.762 9890466.595)   

       fid  xLn_ID          xPt_X         xPt_Y  R_Amn_PendidikanB  \
0        0    1089  463639.416341  9.890597e+06                  4   
1        1    1962  463518.492370  9.890470e+06                  4   
2        2    1789  464204.359690  9.889764e+06                  5   
3        3    1789  464140.171832  9.889873e+06                  6   
4        4    1789  464221.903757  9.889713e+06                  6   
...    ...     ...            ...           ...                ...   
1606  1606     786  466579.022294  9.889950e+06                  8   
1607  1607     748  466532.121657  9.889882e+06                  8   
1608  1608     750  466429.025528  9.889908e+06                  3   
1609  1609     839  466363.892863  9.889707e+06                  2   
1610  1610    1650  466675.828070  9.890466e+06                  8   

      R_Amn_PendidikanB_W  ...  S01_O  S01_D      S02_O  S02_D        S03_O  \
0             2043.058333  ...    0.0    0.0  58.980000    0.0  1474.500000   
1             2043.058333  ...    0.0    0.0  28.000000    0.0   700.000000   
2             1405.333333  ...    0.0    0.0  21.600000    0.0   540.000000   
3             1818.666667  ...    0.0    0.0   3.956667    0.0    98.916667   
4             1846.383333  ...    0.0    0.0   9.426667    0.0   235.666667   
...                   ...  ...    ...    ...        ...    ...          ...   
1606          2019.758333  ...    0.0    0.0   1.000000    0.0     5.000000   
1607          2019.758333  ...    0.0    0.0   1.000000    0.0     5.000000   
1608           785.333333  ...    0.0    0.0   1.000000    0.0     5.000000   
1609           518.666667  ...    0.0    0.0   1.000000    0.0     5.000000   
1610          2025.091667  ...    0.0    0.0   1.000000    0.0     5.000000   

            S03_D       S04_O  S04_D  Strg_700  Strg_1200  
0     1474.500000  147.450000    0.0  0.736216   0.751492  
1      700.000000   70.000000    0.0  0.730009   0.735413  
2      540.000000   54.000000    0.0  0.678873   0.751894  
3       98.916667    9.891667    0.0  0.724186   0.768051  
4      235.666667   23.566667    0.0  0.692498   0.768184  
...           ...         ...    ...       ...        ...  
1606     5.000000    2.500000    0.0  0.722584   0.728360  
1607     5.000000    2.500000    0.0  0.732459   0.722508  
1608     5.000000    2.500000    0.0  0.633226   0.644482  
1609     5.000000    2.500000    0.0  0.693805   0.602139  
1610     5.000000    2.500000    0.0  0.684456   0.754923  

[1611 rows x 54 columns]

In [7]:
nwSim.EntriesDf.to_file(MainDir+"1B_01_rslt.gpkg", layer="EntriesQlt", crs="EPSG:32750", driver='GPKG')
nwSim.NetworkDf.to_file(MainDir+"1B_01_rslt.gpkg", layer="NetworkQlt", crs="EPSG:32750", driver='GPKG')

In [3]:
dfnw = gpd.read_file(MainDir+"1B_01_rslt.gpkg", layer="NetworkQlt")
dfnw

Tipe  Mult    EdgeCost  EdgePtSt  EdgePtEd      Sim_01  \
0     Green Comunity   1.0   10.828174         0         1    4.092832   
1      Internal_Road   1.0  524.712277         2         3    7.200000   
2      Internal_Road   1.0   39.002798         3         4    8.703663   
3      Internal_Road   1.0  234.877336         4         1    8.961962   
4      Internal_Road   1.0  207.203690         1         5    9.001134   
...              ...   ...         ...       ...       ...         ...   
2551         Trotoar   1.0  596.886782      1710      1708    8.159475   
2552         Trotoar   1.0  101.039093      1449       265  121.767296   
2553         Trotoar   1.0    5.991789      1422      1423   78.872873   
2554           Cross   2.0   48.079128       270      1315  184.727379   
2555         Trotoar   1.0  258.093462      1315      1711  128.846163   

           Sim_02       Sim_03      Sim_04  Btw_Commute  Btw_Activity  \
0        7.887928    11.242394    2.319979    23.961520     13.562373   
1        3.780000   218.247024    9.450000    21.960000    227.697024   
2       48.960000    39.212720   14.400000   115.327326     53.612720   
3       32.640000    31.766840    9.600000    83.203923     41.366840   
4       41.072072    34.294582   12.080021   100.146411     46.374603   
...           ...          ...         ...          ...           ...   
2551     0.000000    35.626526    0.000000    16.318949     35.626526   
2552   448.236028  1282.721926  179.309136  1140.006649   1462.031062   
2553  1152.157145   830.827704  448.983623  2462.060036   1279.811326   
2554  1148.081320   810.906688  593.661435  2665.617397   1404.568123   
2555   506.306487  1240.026829  187.742717  1270.305299   1427.769546   

        Btw_Total  Btw_PbTransport      Precinct  \
0       37.523893        18.095836          Nope   
1      249.657024        17.010000     Education   
2      168.940046       112.320000     Education   
3      124.570763        74.880000     Education   
4      146.521014        94.224164     Education   
...           ...              ...           ...   
2551    51.945475         0.000000  MICE & Sport   
2552  2602.037711      1075.781192  MICE & Sport   
2553  3741.871362      2753.297912  MICE & Sport   
2554  4070.185520      2889.824074  MICE & Sport   
2555  2698.074845      1200.355690  MICE & Sport   

                                               geometry  
0     LINESTRING (463927.775 9889818.059, 463923.658...  
1     LINESTRING (463586.175 9890132.407, 463596.127...  
2     LINESTRING (463777.193 9889987.045, 463778.739...  
3     LINESTRING (463779.698 9889948.414, 463779.289...  
4     LINESTRING (463923.658 9889808.044, 463969.175...  
...                                                 ...  
2551  LINESTRING (463147.631 9891643.361, 463149.705...  
2552  LINESTRING (463156.790 9891614.630, 463137.437...  
2553  LINESTRING (463167.124 9891629.372, 463168.043...  
2554  LINESTRING (463085.410 9891388.770, 463061.373...  
2555  LINESTRING (463061.373 9891388.402, 463061.206...  

[2556 rows x 15 columns]

In [5]:
sets = [
    ['Btw_Commute', 8.0, 1, 0.8],
    ['Btw_Activity', 12.0, 2.5, 1.1],
    ['Btw_Commute', 17.0, 1.2, 1.05],
]
sp = 0.5

rslt = sna.SimTimeDistribute(dfnw, sets, spread=sp)
rslt.head()

HrTrf_0.0  HrTrf_0.5  HrTrf_1.0  HrTrf_1.5     HrTrf_2.0     HrTrf_2.5  \
0   0.000051   0.000019   0.000007   0.000002  8.265971e-07  3.356745e-07   
1   0.000833   0.000316   0.000115   0.000041  1.387706e-05  5.631392e-06   
2   0.000203   0.000075   0.000027   0.000010  3.267610e-06  1.327165e-06   
3   0.000156   0.000058   0.000021   0.000007  2.521234e-06  1.023959e-06   
4   0.000175   0.000065   0.000024   0.000008  2.826459e-06  1.147992e-06   

      HrTrf_3.0  HrTrf_3.5  HrTrf_4.0  HrTrf_4.5  ...  HrTrf_19.0  HrTrf_19.5  \
0  4.676383e-07   0.000002   0.000025   0.000349  ...    4.037051    1.999992   
1  7.602467e-06   0.000031   0.000145   0.000810  ...    5.123648    2.636678   
2  1.862069e-06   0.000010   0.000113   0.001653  ...   19.353272    9.582459   
3  1.432968e-06   0.000008   0.000083   0.001199  ...   13.980365    6.923385   
4  1.610931e-06   0.000009   0.000098   0.001435  ...   16.804541    8.320413   

   HrTrf_20.0  HrTrf_20.5  HrTrf_21.0  HrTrf_21.5  HrTrf_22.0  HrTrf_22.5  \
0    0.828485    0.290731    0.087669    0.023276    0.005728    0.001439   
1    1.195278    0.493754    0.194252    0.076196    0.030652    0.012624   
2    3.963896    1.386981    0.415782    0.109053    0.026192    0.006314   
3    2.865231    1.003488    0.301392    0.079363    0.019214    0.004696   
4    3.441749    1.204217    0.360955    0.094652    0.022723    0.005473   

   HrTrf_23.0  HrTrf_23.5  
0    0.000413    0.000139  
1    0.005215    0.002116  
2    0.001725    0.000561  
3    0.001305    0.000429  
4    0.001494    0.000485  

[5 rows x 48 columns]

In [15]:
# testing crowd consistency

dfnw['durAc'] = (0,)*len(dfnw)
for cl in dfnw.columns:
    if cl[:5] == 'HrTrf':
        dfnw['durAc'] += (dfnw[cl] >= 800.0)*0.5
# dfnw['durAc'] = dfnw['durAc']/2

dfnw.to_file(MainDir+"1B_01_rslt_Time.gpkg", layer="DurAc", crs="EPSG:32750", driver='GPKG')

In [10]:
# tersting path length

import bokeh.plotting as bk
from bokeh.io import output_notebook

output_notebook()

lnL = tuple(ft.length for ft in dfnw.geometry)
types = list(dfnw['Tipe'].unique())


qts = (0.10, 0.25, 0.5, 0.75, 0.90)

optdts = []
for n, ty in enumerate(types):
    dff = dfnw[dfnw['Tipe'] == ty]
    dtlg = list(dff['geometry'].length)
    # lt = [sum(dtlg)/len(dtlg)]
    wgtdt = tuple(dtlg * dff['Btw_Total'])
    # dtlg = tuple(dtlg)
    datdic = [(v, ln) for v, ln in zip(list(dff['Btw_Total']), dtlg)]
    datdic.sort(key=lambda x: x[0])
    ttlwg = sum(wgtdt)
    lt = [ttlwg/sum(dtlg)]

    for q in qts:
        basecut = sum(dtlg) * q
        tempsum = 0
        qval = None
        for dt in datdic:
            tempsum += dt[1]
            if tempsum > basecut:
                qval = dt[0]
                break
        lt.append( round(qval,0))
        # lt.append(dtlg[int(round(ltlg*q))])
    optdts.append(lt)

for t, v in zip(types, optdts):
    print(t, v)

dtqt = []

for n in range(6):
    sdt= []
    for n in range(len(types)):
        sdt.append(0)
    dtqt.append(sdt)
    
list([list([0,]*len(types)),]*6)
for nn, d in enumerate(optdts):
    for n, v in enumerate(d):
        dtqt[n][nn] = round(v,0)

print(dtqt)

p = bk.figure(width=500, height=800)
tyn = [n for n in range(len(types))]
p.segment(tyn, dtqt[1], tyn, dtqt[5], line_color="black", line_width=1.5)
p.vbar(tyn,0.3 , dtqt[2], dtqt[4], fill_color='red', line_width=0, fill_alpha=0.8)
p.rect(tyn, dtqt[1],0.3 , 0.01, line_color="black", line_width=1.5)
p.rect(tyn, dtqt[5],0.3 , 0.01, line_color="black", line_width=1.5)
p.rect(tyn, dtqt[3],0.3 , 0.01, line_color="black", line_width=1.5)
p.circle(tyn, dtqt[0], size=6, color="black")

bk.show(p)

Green Comunity [452.9638951309276, 0.0, 26.0, 181.0, 562.0, 1403.0]
Internal_Road [756.6767498445939, 28.0, 110.0, 354.0, 994.0, 1938.0]
Cross [2743.7964425323858, 387.0, 1325.0, 2521.0, 3712.0, 5601.0]
Easement [1853.0116995667627, 275.0, 814.0, 1603.0, 2339.0, 3116.0]
Through Block [1936.2505790825246, 338.0, 892.0, 1668.0, 2691.0, 3856.0]
Bridge [2561.954079578784, 737.0, 1398.0, 2293.0, 3742.0, 4274.0]
Trotoar [2665.430664494008, 170.0, 1089.0, 2257.0, 3678.0, 5501.0]
[[453.0, 757.0, 2744.0, 1853.0, 1936.0, 2562.0, 2665.0], [0.0, 28.0, 387.0, 275.0, 338.0, 737.0, 170.0], [26.0, 110.0, 1325.0, 814.0, 892.0, 1398.0, 1089.0], [181.0, 354.0, 2521.0, 1603.0, 1668.0, 2293.0, 2257.0], [562.0, 994.0, 3712.0, 2339.0, 2691.0, 3742.0, 3678.0], [1403.0, 1938.0, 5601.0, 3116.0, 3856.0, 4274.0, 5501.0]]


In [9]:

sim_col = list(rslt.columns)
rn = [n*sp for n in range(len(sim_col))]

import bokeh.plotting as bk
from bokeh.io import output_notebook

output_notebook()
p = bk.figure(frame_width=1500, frame_height=500)


for i in rslt.index:
    rs = list(rslt.iloc[i])
    p.line(rn, rs, line_width=0.8, alpha=0.3)

avg = [rslt[at].mean() for at in sim_col]

p.line(rn, avg, line_width=3, line_color='red')
bk.show(p)

Loading BokehJS ...

In [17]:
from datetime import datetime as dt
from datetime import timedelta

step = 10
step_m = int(round(0.5*60/step))

lines = []
for d in dfnw.index:
    gmt = dfnw.at[d, 'geometry']
    basetime = dt(2023, 1, 1, 0, 0, 0, 0)
    for atst, edst in zip(sim_col[:-1], sim_col[1:]):
        vSt = rslt.at[d, atst]
        vEd = rslt.at[d, edst]
        vStep = (vEd-vSt)/step
        for nn in range(step):
            val = round((vSt + vStep*nn)*1.0,2)
            tmSt = basetime.strftime("%Y-%m-%d %H:%M:%S")
            # tmSt = basetime
            basetime += timedelta(minutes=step_m)
            tmEd = basetime.strftime("%Y-%m-%d %H:%M:%S")
            lines.append({
                'geometry' : gmt,
                'traffic' : val,
                'tmSt' : tmSt,
                'tmEd' : tmEd
            })
dfopt = gpd.GeoDataFrame(lines)

dfopt.to_file(MainDir+"1B_01_rslt_Time.gpkg", layer="Ttl_sim", crs="EPSG:32750", driver='GPKG')